<a href="https://colab.research.google.com/github/Ismaelfreire/QueimadasPython/blob/main/Projeto_de_Big_Data_em_Python_Mapeamento_de_calor.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

**Queimadas no Ceará: Monitoramento e Análise por Meio de Dados**!

In [ ]:
!pip install folium

In [ ]:
import folium
from folium.plugins import HeatMap
from folium import plugins
import pandas as pd
from IPython.display import display
import ipywidgets as widgets

In [ ]:
dados = pd.read_csv('Basedados.csv')
dados.head()

DataHora  Satelite    Pais Estado        Municipio     Bioma  \
0  2023/01/03 16:20:00  AQUA_M-T  Brasil  CEARÁ     PEDRA BRANCA  Caatinga   
1  2023/01/03 16:20:00  AQUA_M-T  Brasil  CEARÁ  PIQUET CARNEIRO  Caatinga   
2  2023/01/03 16:20:00  AQUA_M-T  Brasil  CEARÁ       ALTO SANTO  Caatinga   
3  2023/01/03 16:20:00  AQUA_M-T  Brasil  CEARÁ    INDEPENDÊNCIA  Caatinga   
4  2023/01/03 16:20:00  AQUA_M-T  Brasil  CEARÁ  PIQUET CARNEIRO  Caatinga   

   DiaSemChuva  Precipitacao  RiscoFogo  Latitude  Longitude    FRP  
0            6          0.10       1.00  -5.48604  -39.73949   11.1  
1            0          0.00       0.77  -5.85353  -39.35537    8.1  
2            0          6.41       0.07  -5.53426  -38.08508  136.1  
3            0          2.81       0.43  -5.55035  -40.54355   16.3  
4            7          0.07       0.98  -5.96212  -39.53709   10.7

In [ ]:
baseMap = folium.Map(
    width = '100%',
    height = '100%',
    location = [-5.498397, -39.320624],
    zoom_start = 7)
baseMap

In [ ]:
coordenadas = dados[['Latitude', 'Longitude']].values.tolist()
coordenadas

[[-5.48604, -39.73949],
 [-5.85353, -39.35537],
 [-5.53426, -38.08508],
 [-5.55035, -40.54355],
 [-5.96212, -39.53709],
 [-6.36226, -38.65899],
 [-6.06538, -39.48725],
 [-5.60458, -39.79661],
 [-3.14678, -41.12151],
 [-3.14833, -41.13214],
 [-3.14967, -41.12632],
 [-3.15117, -41.13701],
 [-6.088, -39.18472],
 [-3.17154, -40.62217],
 [-3.18419, -41.23062],
 [-3.4325, -40.11682],
 [-3.46422, -39.37636],
 [-3.46551, -39.38548],
 [-3.52486, -39.349],
 [-3.52617, -39.35809],
 [-3.77105, -38.69181],
 [-3.90098, -39.53244],
 [-3.90231, -39.5417],
 [-6.0942, -39.1013],
 [-3.9589, -38.39096],
 [-4.03816, -40.42331],
 [-4.03961, -40.43338],
 [-5.54191, -38.07485],
 [-4.04761, -40.42197],
 [-4.17994, -40.32965],
 [-5.64209, -39.67602],
 [-4.38897, -39.59235],
 [-4.45956, -40.35217],
 [-4.46098, -40.3622],
 [-4.50621, -40.89354],
 [-4.52163, -38.2724],
 [-4.52291, -38.28131],
 [-4.55145, -38.03488],
 [-4.62945, -40.6986],
 [-4.75511, -41.217],
 [-5.24532, -40.85148],
 [-5.25837, -38.9205],
 [-5.46

In [ ]:
HeatMap(coordenadas, radius = 15).add_to(baseMap)
baseMap

In [ ]:
# Convertendo a coluna de data para o tipo datetime
dados['DataHora'] = pd.to_datetime(dados['DataHora'])

# Função para criar o mapa com base no mês selecionado
def criar_mapa(mes):
    # Filtrando os dados pelo mês selecionado, ou todos os dados se "Anual" for selecionado
    if mes is None:
        dados_filtrados = dados  # Mapa de calor anual (todos os dados)
    else:
        dados_filtrados = dados[dados['DataHora'].dt.month == mes]

    # Criando o mapa base
    mapa = folium.Map(location=[-5.0, -39.0], zoom_start=7)

    # Preparando os dados para o HeatMap
    heat_data = [[row['Latitude'], row['Longitude'], row['FRP']] for index, row in dados_filtrados.iterrows()]

    # Adicionando o HeatMap ao mapa, apenas se houver dados
    if heat_data:
        HeatMap(heat_data).add_to(mapa)

    # Adicionando círculos ao mapa
    for i in range(len(dados_filtrados)):
        folium.Circle(
            location=[dados_filtrados.iloc[i]['Latitude'], dados_filtrados.iloc[i]['Longitude']],
            color='#808080',
            fill=True,  # Alterado para True para preencher a cor
            fill_color='00A1B3',  # Corrigido para fill_color
            tooltip=(
                '<li><b> Município: </b>' + str(dados_filtrados.iloc[i]['Municipio']) +
                '<li><b> Registro: </b>' + str(dados_filtrados.iloc[i]['DataHora']) +
                '<li><b> Potência Radiativa do Fogo: </b>' + str(dados_filtrados.iloc[i]['FRP'])
            ),
            radius=10
        ).add_to(mapa)

    # Exibindo o mapa
    display(mapa)

# Criando o Dropdown para selecionar o mês ou a opção "Anual"
dropdown_mes = widgets.Dropdown(
    options={
        'Anual': None, 'Janeiro': 1, 'Fevereiro': 2, 'Março': 3, 'Abril': 4, 'Maio': 5, 'Junho': 6,
        'Julho': 7, 'Agosto': 8, 'Setembro': 9, 'Outubro': 10, 'Novembro': 11, 'Dezembro': 12
    },
    value=None,
    description='Mês:'
)

# Conectando o Dropdown à função de criação do mapa
widgets.interactive(criar_mapa, mes=dropdown_mes)


interactive(children=(Dropdown(description='Mês:', options={'Anual': None, 'Janeiro': 1, 'Fevereiro': 2, 'Març…